In [1]:
# 0.1. Cài đặt các thư viện cần thiết
!pip install -q fpdf2 noisereduce librosa tensorflow scikit-learn matplotlib seaborn pytz PyDrive2  


[notice] A new release of pip is available: 23.0.1 -> 25.2
[notice] To update, run: pip install --upgrade pip


In [2]:
# CÀI ĐẶT & CẤU HÌNH (SETUP & CONFIGURATION)
# 0.2. Import thư viện
import os
import glob 
import random
import datetime
import pytz
import shutil
import joblib
import zipfile
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.font_manager as fm
from fpdf import FPDF
from tqdm import tqdm
import librosa
import noisereduce as nr
import tensorflow as tf
from tensorflow.keras import mixed_precision
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense, Dropout, GlobalAveragePooling2D, AveragePooling2D
from tensorflow.keras.applications import EfficientNetB1
from tensorflow.keras.applications.efficientnet import preprocess_input
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint, ReduceLROnPlateau
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.model_selection import StratifiedGroupKFold
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.utils import class_weight
from pydrive2.auth import GoogleAuth
from pydrive2.drive import GoogleDrive
from kaggle_secrets import UserSecretsClient
from oauth2client.service_account import ServiceAccountCredentials
from tensorflow.keras.regularizers import l2
from kaggle_datasets import KaggleDatasets
from sklearn.metrics import roc_curve, auc as sklearn_auc
from sklearn.preprocessing import label_binarize
from itertools import cycle
mixed_precision.set_global_policy('mixed_bfloat16')
from keras.saving import register_keras_serializable

try:
    # Cố gắng kết nối với TPU bằng cách chỉ định tpu='local'
    tpu = tf.distribute.cluster_resolver.TPUClusterResolver(tpu='local')
    print('Đã tìm thấy TPU Resolver.')
    
    # Kết nối và khởi tạo hệ thống TPU
    tf.config.experimental_connect_to_cluster(tpu)
    tf.tpu.experimental.initialize_tpu_system(tpu)
    print('Đã khởi tạo hệ thống TPU.')

    # Tạo strategy
    strategy = tf.distribute.TPUStrategy(tpu)
    print('THÀNH CÔNG: Đã tạo TPUStrategy!')
    print(f'Số lượng nhân (replicas): {strategy.num_replicas_in_sync}')
    
except (ValueError, RuntimeError) as e:
    # Nếu vẫn không tìm thấy TPU, tự động chuyển về chiến lược mặc định
    print(f'Lỗi kết nối TPU: {e}')
    print('Không tìm thấy TPU. Sử dụng chiến lược mặc định cho GPU/CPU.')
    strategy = tf.distribute.get_strategy()

/usr/local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


E0000 00:00:1758338873.441289      74 common_lib.cc:612] Could not set metric server port: INVALID_ARGUMENT: Could not find SliceBuilder port 8471 in any of the 0 ports provided in `tpu_process_addresses`="local"
=== Source Location Trace: === 
learning/45eac/tfrc/runtime/common_lib.cc:230


Đã tìm thấy TPU Resolver.
INFO:tensorflow:Deallocate tpu buffers before initializing tpu system.


INFO:tensorflow:Initializing the TPU system: local


I0000 00:00:1758338892.513493      74 service.cc:148] XLA service 0x57ed229deaf0 initialized for platform TPU (this does not guarantee that XLA will be used). Devices:
I0000 00:00:1758338892.513532      74 service.cc:156]   StreamExecutor device (0): TPU, 2a886c8
I0000 00:00:1758338892.513535      74 service.cc:156]   StreamExecutor device (1): TPU, 2a886c8
I0000 00:00:1758338892.513537      74 service.cc:156]   StreamExecutor device (2): TPU, 2a886c8


...

INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:localhost/replica:0/task:0/device:TPU:5, TPU, 0, 0)


INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:localhost/replica:0/task:0/device:TPU:6, TPU, 0, 0)


INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:localhost/replica:0/task:0/device:TPU:7, TPU, 0, 0)


INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:localhost/replica:0/task:0/device:TPU_SYSTEM:0, TPU_SYSTEM, 0, 0)


THÀNH CÔNG: Đã tạo TPUStrategy!
Số lượng nhân (replicas): 8


In [3]:
# THIẾT LẬP CẤU HÌNH 
# --- Các cấu hình cơ bản ---
SEED = 42
def set_seed(seed_value):
    os.environ['PYTHONHASHSEED'] = str(seed_value)
    #os.environ['TF_DETERMINISTIC_OPS'] = '1'
    random.seed(seed_value)
    np.random.seed(seed_value)
    tf.random.set_seed(seed_value)
set_seed(SEED)

KAGGLE_PROCESSED_DATA_PATH = "/kaggle/input/ngt-spectrogram-id/"
KAGGLE_OUTPUT_PATH = "/kaggle/working/output_results"
os.makedirs(KAGGLE_OUTPUT_PATH, exist_ok=True)

CLASSES_TO_TRAIN = ['covid', 'asthma', 'healthy', 'tuberculosis']
ALL_CLASSES = ['healthy', 'asthma', 'covid', 'tuberculosis']
N_SPLITS = 5
TEST_SPLIT_RATIO = 0.15
USE_DATA_AUGMENTATION = True # Bật/tắt augmentation ở đây
USE_FOCAL_LOSS = True
USE_COSINE_DECAY_RESTARTS = True 

MODEL_ID = f'EfficienetB1_CV_TPU'
MIN_DELTA = 1e-4
SHUFFLE_BUFFER_SIZE = 2048 
GAMMA = 2.0 # Giữ nguyên giá trị tiêu chuẩn

# --- CÁC THAY ĐỔI CHÍNH ---
LEARNING_RATE = 5e-6              # Thay đổi: Giảm LR để ổn định hơn
WEIGHT_DECAY = 3e-3               # Thay đổi: Tăng để chống overfitting mạnh hơn

# Cấu hình cho Cross-Validation
TOTAL_EPOCHS = 500                # Giữ nguyên tổng số epochs tối đa
WARMUP_EPOCHS = 3                 # Thay đổi: Rút ngắn Warmup cho hiệu quả
RESTART_CYCLE_1_EPOCHS = 50       # Thay đổi: Chu kỳ ngắn hơn để khám phá nhiều hơn
PATIENCE_EPOCHS = RESTART_CYCLE_1_EPOCHS + 25 # Thay đổi: Patience = 50

# --- ĐỊNH NGHĨA BATCH SIZE ---
# BATCH_SIZE này là batch size cho mỗi nhân TPU (per-replica)
BATCH_SIZE = 64
# Tính toán GLOBAL_BATCH_SIZE để dùng trong pipeline
# Biến 'strategy' được lấy từ ô code đầu tiên
GLOBAL_BATCH_SIZE = BATCH_SIZE * strategy.num_replicas_in_sync
print(f"Batch size mỗi nhân: {BATCH_SIZE}")
print(f"Global batch size (tổng cộng): {GLOBAL_BATCH_SIZE}")

# INPUT_SHAPE sẽ được cập nhật lại ở ô chuẩn bị dữ liệu
INPUT_SHAPE = (240, 240, 3)
print(f"Input shape: {INPUT_SHAPE}")

Batch size mỗi nhân: 64
Global batch size (tổng cộng): 512
Input shape: (240, 240, 3)


In [ ]:
# KHỞI TẠO CÁC HÀM CẦN THIẾT (PHIÊN BẢN ĐÚNG)

def get_patient_id(filepath, class_name):
    filename = os.path.basename(filepath)
    if class_name.lower() in ['asthma', 'covid', 'healthy']:
        return filename.split('_')[0]
    elif class_name.lower() == 'tuberculosis':
        return '_'.join(filename.split('_')[:-1]).replace('.npy', '')
    else:
        return filename.split('_')[0]

@register_keras_serializable()
class MacroF1Score(tf.keras.metrics.Metric):
    """
    Lớp metric để tính toán Macro F1-Score một cách chính xác trên toàn bộ epoch.
    """
    def __init__(self, num_classes, name='f1_macro', **kwargs):
        super(MacroF1Score, self).__init__(name=name, **kwargs)
        self.num_classes = num_classes
        self.true_positives = self.add_weight(name='tp', shape=(num_classes,), initializer='zeros')
        self.false_positives = self.add_weight(name='fp', shape=(num_classes,), initializer='zeros')
        self.false_negatives = self.add_weight(name='fn', shape=(num_classes,), initializer='zeros')

    def update_state(self, y_true, y_pred, sample_weight=None):
        y_pred_labels = tf.argmax(tf.nn.softmax(y_pred), axis=1)
        y_true_labels = tf.argmax(y_true, axis=1)
        cm = tf.math.confusion_matrix(y_true_labels, y_pred_labels, num_classes=self.num_classes, dtype=tf.float32)
        tp = tf.linalg.diag_part(cm)
        fp = tf.reduce_sum(cm, axis=0) - tp
        fn = tf.reduce_sum(cm, axis=1) - tp
        self.true_positives.assign_add(tp)
        self.false_positives.assign_add(fp)
        self.false_negatives.assign_add(fn)

    def result(self):
        precision = self.true_positives / (self.true_positives + self.false_positives + tf.keras.backend.epsilon())
        recall = self.true_positives / (self.true_positives + self.false_negatives + tf.keras.backend.epsilon())
        f1 = 2 * (precision * recall) / (precision + recall + tf.keras.backend.epsilon())
        macro_f1 = tf.reduce_mean(f1)
        return macro_f1

    def reset_state(self):
        self.true_positives.assign(tf.zeros(self.num_classes))
        self.false_positives.assign(tf.zeros(self.num_classes))
        self.false_negatives.assign(tf.zeros(self.num_classes))

    # Thêm phương thức get_config
    def get_config(self):
        config = super(MacroF1Score, self).get_config()
        config.update({'num_classes': self.num_classes})
        return config

    def reset_state(self):
        # Reset các biến trạng thái về 0 ở đầu mỗi epoch
        self.true_positives.assign(tf.zeros(self.num_classes))
        self.false_positives.assign(tf.zeros(self.num_classes))
        self.false_negatives.assign(tf.zeros(self.num_classes))
def parse_tfrecord_fn(example):
    """Hàm đọc và xử lý một mẫu từ file TFRecord cho EfficientNet."""
    feature_description = {
        'image': tf.io.FixedLenFeature([], tf.string),
        'label': tf.io.FixedLenFeature([], tf.int64),
    }
    example = tf.io.parse_single_example(example, feature_description)
    image = tf.io.parse_tensor(example['image'], out_type=tf.float32)
    
    original_shape = (256, 126) 
    image = tf.reshape(image, original_shape)
    image_3d = tf.stack([image, image, image], axis=-1)
    
    # --- BƯỚC CHUẨN HÓA MỚI ĐƯỢC THÊM VÀO ---
    # 1. Chuyển dải giá trị của spectrogram về [0, 1]
    min_val = tf.reduce_min(image_3d)
    max_val = tf.reduce_max(image_3d)
    image_scaled_01 = (image_3d - min_val) / (max_val - min_val + tf.keras.backend.epsilon())
    
    # 2. Chuyển dải giá trị từ [0, 1] sang [0, 255] giống như một ảnh thông thường
    image_scaled_255 = image_scaled_01 * 255.0
    # --------------------------------------------
    
    # Resize ảnh về kích thước mong muốn
    image_resized = tf.image.resize(image_scaled_255, [INPUT_SHAPE[0], INPUT_SHAPE[1]])
    
    # Bây giờ mới đưa vào hàm tiền xử lý chuyên dụng của EfficientNet
    image_preprocessed = preprocess_input(image_resized)
    
    label_encoded = tf.cast(example['label'], tf.int32)
    label_onehot = tf.one_hot(label_encoded, depth=len(ALL_CLASSES))
    
    return image_preprocessed, label_onehot

def augment(spectrogram, label):
    spectrogram = spec_augment(spectrogram)
    return spectrogram, label

def focal_loss_from_logits_optimized(alpha, gamma=2.0):
    # Hàm khởi tạo (factory function) để tạo ra hàm Focal Loss.
    # Chuyển đổi alpha thành một hằng số tensor để tối ưu hóa tính toán.
    alpha = tf.constant(alpha, dtype=tf.float32)

    # Định nghĩa hàm loss thực tế sẽ được Keras sử dụng.
    def focal_loss_fixed(y_true, y_pred):
        # Tính toán Focal Loss từ logits của mô hình.
        # Tính toán cross-entropy tiêu chuẩn từ logits. Việc này ổn định hơn về mặt số học.
        cross_entropy = tf.nn.softmax_cross_entropy_with_logits(labels=y_true, logits=y_pred)
        
        # Chuyển đổi logits thành xác suất để tính toán hệ số điều biến.
        probs = tf.nn.softmax(y_pred)
        
        # Tính pt - xác suất của lớp đúng (true class).
        pt = tf.reduce_sum(y_true * probs, axis=-1)
        
        # Tính toán hệ số điều biến (modulating factor), đây là thành phần cốt lõi của Focal Loss.
        # Hệ số này sẽ giảm loss của các mẫu dễ (pt -> 1) và giữ nguyên loss của các mẫu khó (pt -> 0).
        focal_term = (1.0 - pt) ** gamma
        
        # Áp dụng trọng số alpha tương ứng với lớp đúng của mỗi mẫu.
        alpha_t = tf.reduce_sum(y_true * alpha, axis=-1)
        
        # Loss cuối cùng là cross-entropy được điều chỉnh bởi cả hai hệ số alpha_t và focal_term.
        loss = alpha_t * focal_term * cross_entropy
        
        # Trả về giá trị loss trung bình trên toàn bộ batch.
        return tf.reduce_mean(loss)
        
    # Trả về hàm loss đã được cấu hình với alpha và gamma.
    return focal_loss_fixed

def spec_augment(spectrogram, time_masking_para=40, frequency_masking_para=30, num_time_masks=1, num_freq_masks=1):
    spectrogram_aug = spectrogram
    freq_bins = tf.shape(spectrogram)[1] # Sửa: Lấy chiều tần số từ shape 4D
    time_steps = tf.shape(spectrogram)[2] # Sửa: Lấy chiều thời gian từ shape 4D
    
    for _ in range(num_freq_masks):
        f = tf.random.uniform(shape=(), minval=0, maxval=frequency_masking_para, dtype=tf.int32)
        f0 = tf.random.uniform(shape=(), minval=0, maxval=freq_bins - f, dtype=tf.int32)
        freq_mask_1d = tf.concat([tf.ones((f0,), dtype=spectrogram.dtype), tf.zeros((f,), dtype=spectrogram.dtype), tf.ones((freq_bins - f0 - f,), dtype=spectrogram.dtype)], axis=0)
        freq_mask_4d = tf.reshape(freq_mask_1d, (1, freq_bins, 1, 1)) # Sửa: Reshape thành 4D để broadcast
        spectrogram_aug *= freq_mask_4d
        
    for _ in range(num_time_masks):
        t = tf.random.uniform(shape=(), minval=0, maxval=time_masking_para, dtype=tf.int32)
        t0 = tf.random.uniform(shape=(), minval=0, maxval=time_steps - t, dtype=tf.int32)
        time_mask_1d = tf.concat([tf.ones((t0,), dtype=spectrogram.dtype), tf.zeros((t,), dtype=spectrogram.dtype), tf.ones((time_steps - t0 - t,), dtype=spectrogram.dtype)], axis=0)
        time_mask_4d = tf.reshape(time_mask_1d, (1, 1, time_steps, 1)) # Sửa: Reshape thành 4D để broadcast
        spectrogram_aug *= time_mask_4d
        
    return spectrogram_aug

@register_keras_serializable()
class FinalModel(tf.keras.Model):
    # --- PHƯƠNG THỨC KHỞI TẠO ---
    # Đây là nơi định nghĩa tất cả các lớp (layers) mà mô hình sẽ sử dụng.
    def __init__(self, input_shape, num_classes, **kwargs):
        super(FinalModel, self).__init__(**kwargs)
        
        # Lưu lại cấu hình để có thể lưu và tải mô hình
        self.input_shape_config = input_shape
        self.num_classes_config = num_classes
        
        # --- 1. MÔ HÌNH NỀN (BACKBONE) ---
        # Sử dụng EfficientNetB1 làm bộ trích xuất đặc trưng chính.
        self.base_model = EfficientNetB1(
            # Tải về các trọng số đã được huấn luyện trước trên bộ dữ liệu ImageNet.
            weights='imagenet',
            
            # Bỏ đi lớp phân loại cuối cùng của EfficientNet (vốn dùng để phân loại 1000 lớp của ImageNet).
            # Chúng tôi sẽ thay thế nó bằng các lớp phân loại của riêng mình.
            include_top=False,
            
            # Xác định kích thước của ảnh đầu vào (trong trường hợp này là ảnh spectrogram).
            input_shape=self.input_shape_config
        )
        
        # --- 2. CÁC LỚP "HEAD" PHÂN LOẠI ---
        # Đây là các lớp tùy chỉnh được thêm vào sau mô hình nền.
        
        # GlobalAveragePooling2D: Chuyển đổi đầu ra đa chiều của mô hình nền thành một vector đặc trưng duy nhất.
        # Giúp giảm số lượng tham số và kiểm soát overfitting.
        self.pooling = GlobalAveragePooling2D()
        
        # Dense (Fully Connected): Một lớp ẩn giúp mô hình học các mối liên hệ phức tạp hơn giữa các đặc trưng.
        self.dense1 = Dense(
            256,  # Số lượng nơ-ron trong lớp.
            activation='relu',  # Hàm kích hoạt phi tuyến tính phổ biến.
            # kernel_regularizer=l2(0.001): Kỹ thuật điều chuẩn L2 để "phạt" các trọng số quá lớn, giúp chống overfitting.
            kernel_regularizer=l2(0.001)
        )
        
        # Dropout: Một kỹ thuật điều chuẩn (regularization) mạnh mẽ khác.
        # Trong quá trình huấn luyện, nó sẽ ngẫu nhiên "tắt" 50% các nơ-ron để ngăn mô hình quá phụ thuộc vào một vài nơ-ron nhất định.
        self.dropout = Dropout(0.5)
        
        # Dense (Output Layer): Lớp đầu ra cuối cùng của mô hình.
        self.dense_output = Dense(
            num_classes,  # Số nơ-ron bằng với số lớp bệnh cần chẩn đoán.
            # activation='linear': Xuất ra các giá trị điểm thô (logits) thay vì xác suất.
            # Việc này giúp tăng tính ổn định về mặt số học khi hàm softmax được tích hợp trong hàm loss.
            activation='linear',
            # dtype='float32': Đảm bảo đầu ra có độ chính xác 32-bit.
            dtype='float32'
        )

    # --- PHƯƠNG THỨC CALL ---
    # Đây là nơi chúng tôi định nghĩa luồng đi của dữ liệu qua các lớp (forward pass).
    def call(self, inputs, training=None):
        # Dữ liệu đi qua mô hình nền để trích xuất đặc trưng.
        x = self.base_model(inputs, training=training)
        
        # Dữ liệu đi qua các lớp "Head" để phân loại.
        x = self.pooling(x)
        x = self.dense1(x)
        x = self.dropout(x, training=training)
        
        # Trả về kết quả cuối cùng (logits).
        outputs = self.dense_output(x)
        return outputs

    # --- PHƯƠNG THỨC GET_CONFIG ---
    # Giúp Keras biết cách tái tạo lại mô hình khi bạn lưu nó dưới dạng file.
    # Nó lưu lại các tham số quan trọng đã được truyền vào lúc khởi tạo.
    def get_config(self):
        config = super(FinalModel, self).get_config()
        config.update({
            'input_shape': self.input_shape_config,
            'num_classes': self.num_classes_config
        })
        return config

def load_data_from_df(df):
    X, y = [], []
    for _, row in df.iterrows():
        X.append(np.load(row['filepath']))
        y.append(row['label'])
    return np.array(X), np.array(y)

def get_grad_cam_final(model, img_array, last_conv_layer_name, pred_index=None):
    """
    Tạo Grad-CAM cho một subclassed model.
    Lưu ý: Model phải được build (chạy qua dữ liệu một lần) trước khi gọi hàm này.
    """
    # Tạo một model trung gian với input là input của model chính,
    # và output là lớp conv cuối và output cuối cùng của model chính.
    grad_model = Model(
        inputs=model.inputs,
        outputs=[model.base_model.get_layer(last_conv_layer_name).output, model.output]
    )

    # Tính toán gradient
    with tf.GradientTape() as tape:
        # Đưa ảnh vào grad_model để lấy 2 output đã định nghĩa ở trên
        last_conv_layer_output, preds = grad_model(img_array)
        
        if pred_index is None:
            pred_index = tf.argmax(preds[0])
        class_channel = preds[:, pred_index]

    # Lấy gradient của lớp được dự đoán đối với feature map của lớp conv cuối
    grads = tape.gradient(class_channel, last_conv_layer_output)

    # Tính trung bình gradient và tạo heatmap
    pooled_grads = tf.reduce_mean(grads, axis=(0, 1, 2))
    last_conv_layer_output = last_conv_layer_output[0]
    heatmap = last_conv_layer_output @ pooled_grads[..., tf.newaxis]
    heatmap = tf.squeeze(heatmap)
    
    heatmap = tf.maximum(heatmap, 0) / (tf.math.reduce_max(heatmap) + tf.keras.backend.epsilon())
    
    return heatmap.numpy()

def overlay_grad_cam(spec, heatmap, alpha=0.6):
    heatmap_resized = tf.image.resize(heatmap[..., np.newaxis], (spec.shape[0], spec.shape[1]))
    heatmap_resized = np.uint8(255 * heatmap_resized)
    jet = plt.cm.get_cmap("jet")
    jet_colors = jet(np.arange(256))[:, :3]
    jet_heatmap = jet_colors[heatmap_resized.squeeze()]
    spec_display = np.stack([spec]*3, axis=-1)
    spec_display = (spec_display - spec_display.min()) / (spec_display.max() - spec_display.min())
    superimposed_img = jet_heatmap * alpha + spec_display
    superimposed_img = np.clip(superimposed_img, 0, 1)
    return superimposed_img

class PDFReport(FPDF):
    def header(self):
        self.set_font('Arial', 'B', 12)
        self.cell(0, 10, 'BAO CAO KET QUA HUAN LUYEN MO HINH AI', 0, 1, 'C')
        self.ln(10)
    def footer(self):
        self.set_y(-15)
        self.set_font('Arial', 'I', 8)
        self.cell(0, 10, f'Trang {self.page_no()}', 0, 0, 'C')
    def chapter_title(self, title):
        self.set_font('Arial', 'B', 12)
        self.cell(0, 10, title, 0, 1, 'L')
        self.ln(5)
    def chapter_body(self, content):
        self.set_font('Arial', '', 10)
        safe_content = content.encode('latin-1', 'replace').decode('latin-1')
        self.multi_cell(0, 5, safe_content)
        self.ln()
    def add_image_section(self, title, img_path):
        self.chapter_title(title)
        if os.path.exists(img_path):
            self.image(img_path, x=None, y=None, w=180)
            self.ln(5)
        else:
            self.chapter_body(f"Khong tim thay hinh anh: {img_path}")

def authenticate_gdrive():
    user_secrets = UserSecretsClient()
    secret_value = user_secrets.get_secret("google_service_account_key")
    with open("service_account.json", "w") as f:
        f.write(secret_value)
    scope = ["https://www.googleapis.com/auth/drive"]
    gauth = GoogleAuth()
    gauth.credentials = ServiceAccountCredentials.from_json_keyfile_name("service_account.json", scope)
    drive = GoogleDrive(gauth)
    return drive

def upload_folder_to_drive(drive, folder_path, parent_folder_id):
    folder_name = os.path.basename(folder_path)
    print(f"Đang tạo thư mục '{folder_name}' trên Google Drive...")
    folder_metadata = {'title': folder_name, 'mimeType': 'application/vnd.google-apps.folder', 'parents': [{'id': parent_folder_id}]}
    folder = drive.CreateFile(folder_metadata)
    folder.Upload()
    
    print(f"Bắt đầu tải nội dung của '{folder_name}'...")
    for item in tqdm(os.listdir(folder_path), desc=f"Uploading {folder_name}"):
        item_path = os.path.join(folder_path, item)
        if os.path.isfile(item_path):
            gfile = drive.CreateFile({'title': item, 'parents': [{'id': folder['id']}]})
            gfile.SetContentFile(item_path)
            gfile.Upload(param={'supportsTeamDrives': True})
        elif os.path.isdir(item_path):
            upload_folder_to_drive(drive, item_path, folder['id'])

def _bytes_feature(value):
    """Returns a bytes_list from a string / byte."""
    if isinstance(value, type(tf.constant(0))):
        value = value.numpy()
    return tf.train.Feature(bytes_list=tf.train.BytesList(value=[value]))

def _int64_feature(value):
    """Returns an int64_list from a bool / enum / int / uint."""
    return tf.train.Feature(int64_list=tf.train.Int64List(value=[value]))

def serialize_example(image, label):
    """Creates a tf.train.Example message ready to be written to a file."""
    feature = {
        'image': _bytes_feature(tf.io.serialize_tensor(image)),
        'label': _int64_feature(label)
    }
    example_proto = tf.train.Example(features=tf.train.Features(feature=feature))
    return example_proto.SerializeToString()
class LearningRateLogger(tf.keras.callbacks.Callback):
    def on_epoch_begin(self, epoch, logs=None):
        current_lr = tf.keras.backend.get_value(self.model.optimizer.learning_rate)
        print(f"\nEpoch {epoch+1}: Learning Rate is {current_lr:.2e}")

In [5]:
# CHUẨN BỊ DỮ LIỆU VÀ TẠO TFRECORD
suspicious_files_to_remove = [
    '/kaggle/input/ngt-spectrogram-id/healthy/P0030101_123370_Dkwg3F7jMGaR7kbc-seg2.npy',
    '/kaggle/input/ngt-spectrogram-id/covid/P0032202_15897_PcbyJQWemBfghUYp-seg2.npy',
    '/kaggle/input/ngt-spectrogram-id/covid/P0027142_5701_hupBI5CxKMNCfe8b-seg1.npy',
    '/kaggle/input/ngt-spectrogram-id/covid/P0056214_89533_0WsmNRSKuQFGodg1-seg1.npy',
]
# --- BƯỚC 1: TẢI VÀ PHÂN CHIA DỮ LIỆU BAN ĐẦU ---
print("Bắt đầu chuẩn bị và phân chia dữ liệu...")
all_files_to_split = []
for class_name in ALL_CLASSES:
    source_dir = os.path.join(KAGGLE_PROCESSED_DATA_PATH, class_name)
    if os.path.exists(source_dir):
        files = glob.glob(os.path.join(source_dir, '*.npy'))
        for f in files:
            all_files_to_split.append({'filepath': f, 'label': class_name})

all_data_df = pd.DataFrame(all_files_to_split)
all_data_df['patient_id'] = all_data_df.apply(lambda row: get_patient_id(row['filepath'], row['label']), axis=1)

print(f"Số lượng mẫu ban đầu: {len(all_data_df)}")
all_data_df = all_data_df[~all_data_df['filepath'].isin(suspicious_files_to_remove)].reset_index(drop=True)
print(f"Số lượng mẫu sau khi lọc bỏ file 'im lặng': {len(all_data_df)}")

print("Tách tập Test cuối cùng (Hold-out set)...")
patient_ids = all_data_df['patient_id'].unique()
np.random.shuffle(patient_ids)
test_patient_count = int(len(patient_ids) * TEST_SPLIT_RATIO)
test_patients = patient_ids[:test_patient_count]
train_val_patients = patient_ids[test_patient_count:]

test_df = all_data_df[all_data_df['patient_id'].isin(test_patients)].reset_index(drop=True)
train_val_df = all_data_df[all_data_df['patient_id'].isin(train_val_patients)].reset_index(drop=True)

print(f"Đã tách: {len(train_val_df)} mẫu cho Train/Validation (CV) và {len(test_df)} mẫu cho Test cuối cùng.")

# --- BƯỚC 2: KHỞI TẠO LABEL ENCODER VÀ STANDARD SCALER ---
le = LabelEncoder().fit(ALL_CLASSES)
# Cập nhật INPUT_SHAPE từ một file mẫu

# --- BƯỚC 3: CHUYỂN ĐỔI DỮ LIỆU SANG ĐỊNH DẠNG TFRECORD ---
TFRECORD_OUTPUT_PATH = "/kaggle/working/tfrecords"
os.makedirs(TFRECORD_OUTPUT_PATH, exist_ok=True)
print(f"Bắt đầu chuyển đổi dữ liệu sang TFRecord tại: {TFRECORD_OUTPUT_PATH}")

all_dfs = {'train_val': train_val_df, 'test': test_df}

for df_name, df in all_dfs.items():
    print(f"--- Đang xử lý tập {df_name} ---")
    tfrecord_path = os.path.join(TFRECORD_OUTPUT_PATH, f"{df_name}.tfrec")
    
    with tf.io.TFRecordWriter(tfrecord_path) as writer:
        # Sử dụng tqdm tiêu chuẩn để tránh lỗi ImportError
        for _, row in tqdm(df.iterrows(), total=len(df), desc=f"Creating {df_name}.tfrec"):
            spectrogram = np.load(row['filepath']).astype(np.float32)
            label_encoded = le.transform([row['label']])[0]
            
            example = serialize_example(spectrogram, label_encoded)
            writer.write(example)
            
print("\nChuyển đổi sang TFRecord hoàn tất!")

Bắt đầu chuẩn bị và phân chia dữ liệu...


Số lượng mẫu ban đầu: 33084


Số lượng mẫu sau khi lọc bỏ file 'im lặng': 33080
Tách tập Test cuối cùng (Hold-out set)...


Đã tách: 28060 mẫu cho Train/Validation (CV) và 5020 mẫu cho Test cuối cùng.


Bắt đầu chuyển đổi dữ liệu sang TFRecord tại: /kaggle/working/tfrecords
--- Đang xử lý tập train_val ---


...


Creating test.tfrec: 100%|█████████▉| 4995/5020 [01:01<00:00, 78.19it/s]


Creating test.tfrec: 100%|█████████▉| 5004/5020 [01:01<00:00, 80.02it/s]


Creating test.tfrec: 100%|█████████▉| 5013/5020 [01:01<00:00, 81.17it/s]


Creating test.tfrec: 100%|██████████| 5020/5020 [01:02<00:00, 80.95it/s]


Chuyển đổi sang TFRecord hoàn tất!


In [6]:
# HUẤN LUYỆN MÔ HÌNH Cross-Validation

# --- BƯỚC 1: KHỞI TẠO CÁC BIẾN CẦN THIẾT ---
print("Đang khởi tạo các biến cho Cross-Validation...")
AUTOTUNE = tf.data.AUTOTUNE
skf = StratifiedGroupKFold(n_splits=N_SPLITS, shuffle=True, random_state=SEED)
cv_data_to_split = train_val_df[train_val_df['label'].isin(CLASSES_TO_TRAIN)]
X_cv_paths = cv_data_to_split['filepath'].values
y_cv_labels = le.transform(cv_data_to_split['label'])
groups_cv = cv_data_to_split['patient_id'].values

fold_accuracies, fold_losses, fold_aucs, fold_f1s = [], [], [], []

print("Đang tính toán trọng số alpha cho Focal Loss...")
class_weights_array = class_weight.compute_class_weight('balanced', classes=np.unique(y_cv_labels), y=y_cv_labels)
alpha_weights_list = class_weights_array.tolist()
print("Trọng số Alpha được tính toán:")
for i, w in enumerate(alpha_weights_list):
    class_name = le.inverse_transform([i])[0]
    print(f"- Lớp '{class_name}': {w:.2f}")

# --- BƯỚC 2: BẮT ĐẦU VÒNG LẶP CROSS-VALIDATION ---
LOCAL_TFRECORD_PATH = TFRECORD_OUTPUT_PATH
TRAIN_VAL_TFREC = os.path.join(LOCAL_TFRECORD_PATH, 'train_val.tfrec')
print(f"Sẵn sàng đọc dữ liệu TFRecord từ: {TRAIN_VAL_TFREC}")

for fold, (train_indices, val_indices) in enumerate(skf.split(X_cv_paths, y_cv_labels, groups_cv)):
    fold_number = fold + 1
    print("-" * 50 + f"\nBắt đầu Fold {fold_number}/{N_SPLITS}\n" + "-" * 50)
    # TÍNH TOÁN CÁC BƯỚC CHO SCHEDULER
    # 1. Tạo pipeline dữ liệu trước
    train_indices_tf = tf.constant(train_indices, dtype=tf.int64)
    val_indices_tf = tf.constant(val_indices, dtype=tf.int64)
    full_ds = tf.data.TFRecordDataset(TRAIN_VAL_TFREC).enumerate()
    train_ds = full_ds.filter(lambda i, data: tf.reduce_any(i == train_indices_tf)).map(lambda i, data: data)
    val_ds = full_ds.filter(lambda i, data: tf.reduce_any(i == val_indices_tf)).map(lambda i, data: data)
    train_ds = train_ds.map(parse_tfrecord_fn, num_parallel_calls=AUTOTUNE)
    val_ds = val_ds.map(parse_tfrecord_fn, num_parallel_calls=AUTOTUNE)
    train_ds = train_ds.shuffle(buffer_size=SHUFFLE_BUFFER_SIZE).repeat().batch(GLOBAL_BATCH_SIZE).prefetch(buffer_size=AUTOTUNE)
    val_ds = val_ds.cache().batch(GLOBAL_BATCH_SIZE).prefetch(buffer_size=AUTOTUNE)
    
    # 2. Bây giờ mới tính toán steps_per_epoch
    steps_per_epoch = len(train_indices) // GLOBAL_BATCH_SIZE
    validation_steps = len(val_indices) // GLOBAL_BATCH_SIZE
    print(f"Số bước mỗi epoch: {steps_per_epoch} | Số bước validation: {validation_steps}")


    # --- TẠO MODEL VÀ LOSS FUNCTION ---
    with strategy.scope():
        model = FinalModel(input_shape=INPUT_SHAPE, num_classes=len(ALL_CLASSES))
        if USE_FOCAL_LOSS:
            loss_function = focal_loss_from_logits_optimized(alpha=alpha_weights_list, gamma=GAMMA)
        else:
            loss_function = tf.keras.losses.CategoricalCrossentropy(from_logits=True)

    # --- GIAI ĐOẠN 1: HUẤN LUYỆN CÁC LỚP CUỐI (HEAD TRAINING) ---
    print("\n--- Bắt đầu Giai đoạn 1: Huấn luyện các lớp cuối ---")
    with strategy.scope():
        # Đóng băng toàn bộ mô hình nền
        model.base_model.trainable = False
        # Compile với learning rate lớn hơn (ví dụ 1e-3)
        optimizer_head = tf.keras.optimizers.AdamW(learning_rate=1e-4, weight_decay=WEIGHT_DECAY, clipnorm=1.0)
        model.compile(optimizer=optimizer_head, loss=loss_function, metrics=['accuracy', tf.keras.metrics.AUC(name='auc')])
        # Huấn luyện trong 5 epochs
        model.fit(train_ds, validation_data=val_ds, epochs=5,
              steps_per_epoch=steps_per_epoch, validation_steps=validation_steps, verbose=1)

    # --- GIAI ĐOẠN 2: WARMUP VÀ HUẤN LUYỆN CHÍNH VỚI RESTART ---
    print("\n--- Bắt đầu Giai đoạn 2: Fine-tuning ---")

    # 1. THIẾT LẬP CÁC SIÊU THAM SỐ MỚI CHO LỊCH TRÌNH
    with strategy.scope():
        # Đếm tổng số lớp trong mô hình nền (EfficientNetB0)
        num_base_layers = len(model.base_model.layers)
        # Tính toán chỉ số của lớp bắt đầu mở băng (từ giữa mô hình trở đi)
        fine_tune_at = int(num_base_layers * 0.7) # 70%
        # Đầu tiên, đặt toàn bộ mô hình nền là không thể huấn luyện
        model.base_model.trainable = False
        # Bây giờ, mở băng các lớp từ chỉ số `fine_tune_at` đến cuối
        for layer in model.base_model.layers[fine_tune_at:]:
            layer.trainable = True
    
        print(f"Tổng số lớp trong base model: {num_base_layers}")
        print(f"Sẽ mở băng và huấn luyện {num_base_layers - fine_tune_at} lớp cuối cùng (bắt đầu từ lớp {fine_tune_at}).")

        f1_macro = MacroF1Score(num_classes=len(ALL_CLASSES), name='f1_macro')

        # 2. GIAI ĐOẠN 2A: WARMUP
        print(f"\n--- Giai đoạn 2A: Bắt đầu Warmup trong {WARMUP_EPOCHS} epochs ---")
        warmup_lr = LEARNING_RATE / 10 # Bắt đầu với LR rất thấp
        optimizer_warmup = tf.keras.optimizers.AdamW(learning_rate=warmup_lr, weight_decay=WEIGHT_DECAY)
        model.compile(optimizer=optimizer_warmup, loss=loss_function, metrics=['accuracy', f1_macro])

        model.fit(
            train_ds, validation_data=val_ds, epochs=WARMUP_EPOCHS,
            steps_per_epoch=steps_per_epoch, validation_steps=validation_steps, verbose=1
        )

        # 3. GIAI ĐOẠN 2B: HUẤN LUYỆN CHÍNH VỚI COSINE DECAY RESTARTS
        print(f"\n--- Giai đoạn 2B: Bắt đầu huấn luyện chính ---")

        # Sử dụng công tắc để chọn optimizer và callbacks
        if USE_COSINE_DECAY_RESTARTS:
            print("Sử dụng scheduler: CosineDecayRestarts")
            first_decay_steps = RESTART_CYCLE_1_EPOCHS * steps_per_epoch
            lr_scheduler = tf.keras.optimizers.schedules.CosineDecayRestarts(
                initial_learning_rate=LEARNING_RATE,
                first_decay_steps=first_decay_steps,
                t_mul=2.0, 
                m_mul=0.9  # Giảm biên độ restart để ổn định hơn
            )
            optimizer_finetune = tf.keras.optimizers.AdamW(learning_rate=lr_scheduler, weight_decay=WEIGHT_DECAY)
            
            # Callbacks cho CosineDecayRestarts
            callbacks = [
                EarlyStopping(
                    monitor='val_f1_macro', mode='max', patience=PATIENCE_EPOCHS,
                    restore_best_weights=True, min_delta=MIN_DELTA, verbose=1
                ),
                LearningRateLogger()
            ]
        else:
            print("Sử dụng scheduler: ReduceLROnPlateau")
            # Optimizer với learning rate ban đầu cố định
            optimizer_finetune = tf.keras.optimizers.AdamW(learning_rate=LEARNING_RATE, weight_decay=WEIGHT_DECAY)
            
            # Callbacks cho ReduceLROnPlateau
            callbacks = [
                EarlyStopping(
                    monitor='val_f1_macro', mode='max', patience=30, # Có thể cần patience dài hơn
                    restore_best_weights=True, min_delta=MIN_DELTA, verbose=1
                ),
                tf.keras.callbacks.ReduceLROnPlateau(
                    monitor='val_f1_macro', mode='max', factor=0.2,
                    patience=10, # Giảm LR nếu F1 không cải thiện trong 10 epochs
                    min_lr=1e-7,
                    verbose=1
                ),
                LearningRateLogger()
            ]

        # Biên dịch lại mô hình với optimizer và metrics cuối cùng
        with strategy.scope():
            model.compile(optimizer=optimizer_finetune, loss=loss_function, metrics=['accuracy', tf.keras.metrics.AUC(name='auc'), f1_macro])
        
        # Huấn luyện mô hình
        history = model.fit(
            train_ds, validation_data=val_ds, epochs=TOTAL_EPOCHS,
            initial_epoch=WARMUP_EPOCHS,
            steps_per_epoch=steps_per_epoch, validation_steps=validation_steps,
            callbacks=callbacks, verbose=1
        )

    # Tạo đường dẫn và tên file để lưu model
    model_save_path = os.path.join(KAGGLE_OUTPUT_PATH, f'{MODEL_ID}_fold_{fold_number}.keras')
    # Lưu lại toàn bộ mô hình (kiến trúc + trọng số)
    model.save(model_save_path)
    # In ra thông báo để xác nhận
    print(f"Đã lưu mô hình cho Fold {fold_number} tại: {model_save_path}")

    # --- VẼ BIỂU ĐỒ VÀ ĐÁNH GIÁ ---
    print("Đang tạo và lưu biểu đồ huấn luyện...")
    plt.figure(figsize=(18, 7))
    plt.suptitle(f'Training Metrics for Fold {fold_number}', fontsize=16)
    
    # --- Biểu đồ cho các chỉ số (Accuracy, AUC, F1-Macro) ---
    plt.subplot(1, 2, 1)
    # Vẽ các chỉ số của tập Train
    plt.plot(history.history['accuracy'], label='Training Accuracy', color='blue', linestyle='-')
    plt.plot(history.history['auc'], label='Training AUC', color='green', linestyle='-')
    plt.plot(history.history['f1_macro'], label='Training F1-Macro', color='red', linestyle='-')
    
    # Vẽ các chỉ số của tập Validation
    plt.plot(history.history['val_accuracy'], label='Validation Accuracy', color='blue', linestyle='--')
    plt.plot(history.history['val_auc'], label='Validation AUC', color='green', linestyle='--')
    plt.plot(history.history['val_f1_macro'], label='Validation F1-Macro', color='red', linestyle='--')
    
    # Cập nhật lại tiêu đề và nhãn
    plt.title('Biểu đồ các chỉ số (Accuracy, AUC, F1-Macro)')
    plt.xlabel('Epoch')
    plt.ylabel('Giá trị')
    plt.legend(loc='lower right')
    plt.grid(True)
    
    # --- Biểu đồ cho Loss ---
    plt.subplot(1, 2, 2)
    plt.plot(history.history['loss'], label='Training Loss', color='orange')
    plt.plot(history.history['val_loss'], label='Validation Loss', color='purple')
    plt.title('Biểu đồ Loss')
    plt.xlabel('Epoch')
    plt.ylabel('Loss')
    plt.legend(loc='upper right')
    plt.grid(True)
    
    # Lưu và đóng hình ảnh
    plot_filename = f'fold_{fold_number}_metrics.png'
    plot_filepath = os.path.join(KAGGLE_OUTPUT_PATH, plot_filename)
    plt.savefig(plot_filepath)
    plt.close()
    
    print(f"Đã lưu biểu đồ cho Fold {fold_number} tại: {plot_filepath}")
    
    # THÊM 4: Sửa lại model.evaluate để nhận đủ 4 giá trị
    loss, accuracy, auc, f1 = model.evaluate(val_ds, verbose=0)
    print(f"Fold {fold_number} - Validation Loss: {loss:.4f}, Validation Accuracy: {accuracy:.4f}, Validation AUC: {auc:.4f}, Validation F1-Macro: {f1:.4f}")
    
    fold_aucs.append(auc)
    fold_losses.append(loss)
    fold_accuracies.append(accuracy)
    fold_f1s.append(f1) # Thêm lưu trữ F1

    # THÊM 5: Sửa lại câu lệnh print cuối cùng
    print("=" * 50 + "\nKết quả Cross-Validation:\n" 
      + f"Validation Accuracy trung bình: {np.mean(fold_accuracies):.4f} +/- {np.std(fold_accuracies):.4f}\n"
      + f"Validation Loss trung bình: {np.mean(fold_losses):.4f} +/- {np.std(fold_losses):.4f}\n"
      + f"Validation AUC trung bình: {np.mean(fold_aucs):.4f} +/- {np.std(fold_aucs):.4f}\n"
      + f"Validation F1-Macro trung bình: {np.mean(fold_f1s):.4f} +/- {np.std(fold_f1s):.4f}\n" # Thêm dòng này
      + "=" * 50)

Đang khởi tạo các biến cho Cross-Validation...


Đang tính toán trọng số alpha cho Focal Loss...


Trọng số Alpha được tính toán:
- Lớp 'asthma': 1.82
- Lớp 'covid': 0.80
- Lớp 'healthy': 0.87
- Lớp 'tuberculosis': 0.96
Sẵn sàng đọc dữ liệu TFRecord từ: /kaggle/working/tfrecords/train_val.tfrec


--------------------------------------------------
Bắt đầu Fold 1/5
--------------------------------------------------


Cause: could not parse the source code of <function <lambda> at 0x7e9ede639510>: found multiple definitions with identical signatures at the location. This error may be avoided by defining each lambda on a single line and with unique argument names. The matching definitions were:
Match 0:
lambda i, data: data

Match 1:
lambda i, data: tf.reduce_any(i == train_indices_tf)

To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert


...


 2/43 ━━━━━━━━━━━━━━━━━━━━ 3:47 6s/step - accuracy: 0.6094 - auc: 0.7527 - f1_macro: 0.1892 - loss: 3.5557


 3/43 ━━━━━━━━━━━━━━━━━━━━ 3:34 5s/step - accuracy: 0.5764 - auc: 0.7461 - f1_macro: 0.1917 - loss: 3.6755


 4/43 ━━━━━━━━━━━━━━━━━━━━ 3:20 5s/step - accuracy: 0.5544 - auc: 0.7409 - f1_macro: 0.1991 - loss: 3.8104


 5/43 ━━━━━━━━━━━━━━━━━━━━ 3:11 5s/step - accuracy: 0.5416 - auc: 0.7381 - f1_macro: 0.2079 - loss: 3.9520


 6/43 ━━━━━━━━━━━━━━━━━━━━ 3:03 5s/step - accuracy: 0.5321 - auc: 0.7355 - f1_macro: 0.2157 - loss: 4.0881

In [ ]:
print("Bắt đầu quy trình Knowledge Distillation (Phiên bản cuối cùng, tối ưu)...")

# ==============================================================================
# BƯỚC 1: TẠO KIẾN THỨC TỪ ENSEMBLE (TIẾT KIỆM BỘ NHỚ & TƯƠNG THÍCH TPU)
# ==============================================================================
print("\n--- Bước 1: Tạo các nhãn mềm từ 5 mô hình thầy giáo ---")

# 1.1. Tạo dataset để lấy dự đoán.
train_val_ds_for_preds = tf.data.TFRecordDataset(TRAIN_VAL_TFREC)
train_val_ds_for_preds = train_val_ds_for_preds.map(parse_tfrecord_fn, num_parallel_calls=AUTOTUNE)
train_val_ds_for_preds = train_val_ds_for_preds.batch(GLOBAL_BATCH_SIZE)
train_val_ds_for_preds = train_val_ds_for_preds.prefetch(buffer_size=AUTOTUNE)

# 1.2. Lặp qua 5 folds để lấy logits.
all_fold_logits = []
print("Đang tải 5 mô hình thầy giáo và lấy dự đoán...")
for fold_number in tqdm(range(1, N_SPLITS + 1), desc="Processing Folds"):
    model_path = os.path.join(KAGGLE_OUTPUT_PATH, f'{MODEL_ID}_fold_{fold_number}.keras')
    with strategy.scope():
        teacher_model = tf.keras.models.load_model(
            model_path, 
            custom_objects={'focal_loss_fixed': focal_loss_from_logits_optimized(alpha=alpha_weights_list)}
        )
    
    # Sử dụng vòng lặp thủ công để tránh lỗi predict trên TPU và lỗi RAM
    logits_list_for_fold = []
    for images, _ in train_val_ds_for_preds:
        batch_logits = teacher_model(images, training=False)
        logits_list_for_fold.append(batch_logits.numpy())
    
    fold_logits = np.concatenate(logits_list_for_fold, axis=0)
    all_fold_logits.append(fold_logits)

# 1.3. Tính trung bình logits (kiến thức tổng hợp của thầy)
num_train_val_samples = len(train_val_df)
mean_logits = np.mean(np.stack(all_fold_logits, axis=0), axis=0)[:num_train_val_samples]
print(f"-> Đã tạo xong kiến thức cho {len(mean_logits)} mẫu.")


# ==============================================================================
# BƯỚC 2 & 3: ĐỊNH NGHĨA STUDENT MODEL VÀ DISTILLER (Giữ nguyên)
# ==============================================================================
print("\n--- Bước 2 & 3: Định nghĩa Student Model và Distiller ---")
# (Hàm create_student_model và class Distiller giữ nguyên như cũ)
def create_student_model(input_shape, num_classes):
    inputs = keras.Input(shape=input_shape)
    x = layers.Conv2D(32, (3, 3), strides=(2, 2), padding="same")(inputs)
    x = layers.BatchNormalization()(x)
    x = layers.Activation("relu")(x)
    x = layers.Conv2D(64, (3, 3), padding="same")(x)
    x = layers.BatchNormalization()(x)
    x = layers.Activation("relu")(x)
    x = layers.MaxPooling2D(3, strides=2)(x)
    x = layers.Conv2D(128, (3, 3), padding="same")(x)
    x = layers.BatchNormalization()(x)
    x = layers.Activation("relu")(x)
    x = layers.GlobalAveragePooling2D()(x)
    x = layers.Dropout(0.4)(x)
    outputs = layers.Dense(num_classes, dtype='float32')(x)
    return keras.Model(inputs, outputs)

class Distiller(keras.Model):
    def __init__(self, student):
        super().__init__()
        self.student = student
    
    def call(self, inputs):
        return self.student(inputs)

    def compile(self, optimizer, metrics, student_loss_fn, distillation_loss_fn, alpha=0.1, temperature=3):
        super().compile(optimizer=optimizer, metrics=metrics)
        self.student_loss_fn = student_loss_fn
        self.distillation_loss_fn = distillation_loss_fn
        self.alpha = alpha
        self.temperature = temperature

    def train_step(self, data):
        x, y = data
        teacher_logits = y["soft"]
        true_labels = y["hard"]
        with tf.GradientTape() as tape:
            student_logits = self.student(x, training=True)
            student_loss = self.student_loss_fn(true_labels, student_logits)
            distillation_loss = self.distillation_loss_fn(
                tf.nn.softmax(teacher_logits / self.temperature, axis=1),
                tf.nn.softmax(student_logits / self.temperature, axis=1),
            )
            loss = self.alpha * student_loss + (1 - self.alpha) * distillation_loss
        trainable_vars = self.student.trainable_variables
        gradients = tape.gradient(loss, trainable_vars)
        self.optimizer.apply_gradients(zip(gradients, trainable_vars))
        self.compiled_metrics.update_state(true_labels, student_logits)
        results = {m.name: m.result() for m in self.metrics}
        results.update({"student_loss": student_loss, "distillation_loss": distillation_loss})
        return results

print("-> Đã định nghĩa xong.")

# ==============================================================================
# BƯỚC 4: HUẤN LUYỆN MÔ HÌNH HỌC SINH (TIẾT KIỆM BỘ NHỚ)
# ==============================================================================
print("\n--- Bước 4: Chuẩn bị Dataset và Huấn luyện ---")

# 4.1. Tạo lại dataset gốc chứa ảnh và nhãn cứng
images_and_hard_labels_ds = tf.data.TFRecordDataset(TRAIN_VAL_TFREC).map(parse_tfrecord_fn)

# 4.2. Tạo dataset chỉ chứa các nhãn mềm (logits của thầy)
soft_labels_ds = tf.data.Dataset.from_tensor_slices(mean_logits)

# 4.3. Kết hợp (zip) chúng lại với nhau
zipped_ds = tf.data.Dataset.zip((images_and_hard_labels_ds, soft_labels_ds))

# 4.4. Map lại thành định dạng (ảnh, {"soft": nhãn mềm, "hard": nhãn cứng})
distillation_ds = zipped_ds.map(
    lambda images_and_hard, soft: (images_and_hard[0], {"hard": images_and_hard[1], "soft": soft})
)

# 4.5. Shuffle và batch cho quá trình huấn luyện
distillation_ds = distillation_ds.shuffle(len(train_val_df)).batch(GLOBAL_BATCH_SIZE).prefetch(buffer_size=AUTOTUNE)

# 4.6. Huấn luyện
with strategy.scope():
    student = create_student_model(input_shape=INPUT_SHAPE, num_classes=len(ALL_CLASSES))
    distiller = Distiller(student=student)
    
    distiller.compile(
        optimizer=keras.optimizers.AdamW(learning_rate=1e-3, weight_decay=1e-4),
        metrics=[keras.metrics.CategoricalAccuracy(name="accuracy"), 
                 tf.keras.metrics.AUC(name='auc', from_logits=True)],
        student_loss_fn=keras.losses.CategoricalCrossentropy(from_logits=True),
        distillation_loss_fn=keras.losses.KLDivergence(),
        alpha=0.2, 
        temperature=5,
    )

history_student = distiller.fit(distillation_ds, epochs=80)

student_model_path = os.path.join(KAGGLE_OUTPUT_PATH, "student_model.keras")
distiller.student.save(student_model_path)
print(f"\nĐã huấn luyện và lưu mô hình học sinh tại: {student_model_path}")

In [ ]:
# ĐÁNH GIÁ SO SÁNH 5-FOLD, ENSEMBLE VÀ MÔ HÌNH HỌC SINH (ĐÃ SỬA LỖI)

print("Bắt đầu quy trình đánh giá toàn diện...")

# --- BƯỚC 1: CHUẨN BỊ DỮ LIỆU TEST (CHỈ LÀM MỘT LẦN) ---
TEST_TFREC = os.path.join(TFRECORD_OUTPUT_PATH, 'test.tfrec')
print(f"Sử dụng dữ liệu test từ: {TEST_TFREC}")

test_ds = tf.data.TFRecordDataset(TEST_TFREC)
test_ds = test_ds.map(parse_tfrecord_fn, num_parallel_calls=AUTOTUNE)
test_ds = test_ds.batch(GLOBAL_BATCH_SIZE)
test_ds = test_ds.prefetch(buffer_size=AUTOTUNE)

y_test_onehot = np.concatenate([label.numpy() for _, label in test_ds], axis=0)
y_test_encoded = np.argmax(y_test_onehot, axis=1)
target_names = le.classes_
n_classes = len(target_names)
run_timestamp = datetime.datetime.now(pytz.timezone('Asia/Ho_Chi_Minh')).strftime("%Y%m%d_%H%M")
report_figs_path = os.path.join(KAGGLE_OUTPUT_PATH, "final_report_figures")
os.makedirs(report_figs_path, exist_ok=True)

# ==============================================================================
# PHẦN 1: ĐÁNH GIÁ ENSEMBLE TỪ 5 FOLDS
# ==============================================================================
print("\n" + "="*30 + "\nPHẦN 1: ĐÁNH GIÁ ENSEMBLE\n" + "="*30)

all_fold_preds_logits = []
for fold_number in range(1, N_SPLITS + 1):
    print(f"  - Lấy dự đoán từ Fold {fold_number}...")
    model_path = os.path.join(KAGGLE_OUTPUT_PATH, f'{MODEL_ID}_fold_{fold_number}.keras')
    with strategy.scope():
        # THÊM `custom_objects` VÀO ĐÂY ĐỂ SỬA LỖI
        teacher_model = tf.keras.models.load_model(
            model_path,
            custom_objects={'focal_loss_fixed': focal_loss_from_logits_optimized(alpha=alpha_weights_list)}
        )
    all_fold_preds_logits.append(teacher_model.predict(test_ds, verbose=0))

mean_logits = np.mean(np.stack(all_fold_preds_logits, axis=0), axis=0)
y_pred_probs_ensemble = tf.nn.softmax(mean_logits).numpy()
y_pred_encoded_ensemble = np.argmax(y_pred_probs_ensemble, axis=1)

print("\nBáo cáo chi tiết của mô hình Ensemble:")
print(classification_report(y_test_encoded, y_pred_encoded_ensemble, target_names=target_names))

# Vẽ Ma trận nhầm lẫn cho Ensemble
cm_ensemble = confusion_matrix(y_test_encoded, y_pred_encoded_ensemble)
plt.figure(figsize=(10, 8))
sns.heatmap(cm_ensemble, annot=True, fmt='d', cmap='Blues', xticklabels=target_names, yticklabels=target_names)
plt.title(f'Ma trận nhầm lẫn (Ensemble trên {N_SPLITS} Folds)', fontsize=16)
plt.ylabel('Nhãn thật'); plt.xlabel('Nhãn dự đoán')
cm_ensemble_path = os.path.join(report_figs_path, f'ensemble_confusion_matrix_{run_timestamp}.png')
plt.savefig(cm_ensemble_path)
plt.show(); plt.close()


# ==============================================================================
# PHẦN 2: ĐÁNH GIÁ MÔ HÌNH HỌC SINH (Phần này đã đúng, giữ nguyên)
# ==============================================================================
print("\n" + "="*30 + "\nPHẦN 2: ĐÁNH GIÁ MÔ HÌNH HỌC SINH\n" + "="*30)

student_model_path = os.path.join(KAGGLE_OUTPUT_PATH, "student_model.keras")

if not os.path.exists(student_model_path):
    print(f"Không tìm thấy mô hình học sinh tại '{student_model_path}'. Bỏ qua bước đánh giá này.")
else:
    print("Đang tải mô hình học sinh...")
    with strategy.scope():
        student_model = tf.keras.models.load_model(student_model_path)
        # Biên dịch lại model để có thể tính toán đầy đủ các metrics
        student_model.compile(
            loss=keras.losses.CategoricalCrossentropy(from_logits=True),
            metrics=['accuracy', tf.keras.metrics.AUC(name='auc'), MacroF1Score(num_classes=n_classes)]
        )

    print("Đang đánh giá mô hình học sinh trên tập test...")
    student_loss, student_acc, student_auc, student_f1 = student_model.evaluate(test_ds, verbose=1)
    
    print("Đang dự đoán với mô hình học sinh...")
    y_pred_probs_student = tf.nn.softmax(student_model.predict(test_ds, verbose=0)).numpy()
    y_pred_encoded_student = np.argmax(y_pred_probs_student, axis=1)

    # --- Lưu kết quả ra file text ---
    student_report_text = classification_report(y_test_encoded, y_pred_encoded_student, target_names=target_names)
    results_filepath = os.path.join(KAGGLE_OUTPUT_PATH, "student_model_evaluation_results.txt")
    with open(results_filepath, "w") as f:
        f.write("--- KET QUA DANH GIA MO HINH HOC SINH ---\n\n")
        f.write(f"Timestamp: {run_timestamp}\n\n")
        f.write(f"Test Loss: {student_loss:.4f}\n")
        f.write(f"Test Accuracy: {student_acc:.4f}\n")
        f.write(f"Test AUC: {student_auc:.4f}\n")
        f.write(f"Test F1-Macro: {student_f1:.4f}\n")
        f.write("\n--- BAO CAO PHAN LOAI CHI TIET ---\n")
        f.write(student_report_text)
    print(f"\nĐã lưu kết quả đánh giá của mô hình học sinh vào file: {results_filepath}")
    print(student_report_text)

    # --- Vẽ biểu đồ riêng cho mô hình học sinh ---
    # 1. Ma trận nhầm lẫn (Học sinh)
    cm_student = confusion_matrix(y_test_encoded, y_pred_encoded_student)
    plt.figure(figsize=(10, 8))
    sns.heatmap(cm_student, annot=True, fmt='d', cmap='Greens', xticklabels=target_names, yticklabels=target_names)
    plt.title('Ma trận nhầm lẫn (Mô hình Học sinh)', fontsize=16)
    plt.ylabel('Nhãn thật'); plt.xlabel('Nhãn dự đoán')
    cm_student_path = os.path.join(report_figs_path, f'student_confusion_matrix_{run_timestamp}.png')
    plt.savefig(cm_student_path)
    plt.show(); plt.close()

    # 2. Đường cong ROC (Học sinh)
    y_test_binarized = label_binarize(y_test_encoded, classes=range(n_classes))
    plt.figure(figsize=(12, 10))
    for i in range(n_classes):
        fpr, tpr, _ = roc_curve(y_test_binarized[:, i], y_pred_probs_student[:, i])
        auc_score = sklearn_auc(fpr, tpr)
        plt.plot(fpr, tpr, lw=2, label=f'Lớp: {target_names[i]} (AUC = {auc_score:.3f})')
    
    plt.plot([0, 1], [0, 1], 'k--', lw=2, label='Chance')
    plt.title('Đường cong ROC (Mô hình Học sinh)', fontsize=16)
    plt.xlabel('False Positive Rate'); plt.ylabel('True Positive Rate')
    plt.legend(loc='lower right'); plt.grid(True)
    roc_student_path = os.path.join(report_figs_path, f'student_roc_curves_{run_timestamp}.png')
    plt.savefig(roc_student_path)
    plt.show(); plt.close()

    print(f"\nĐã hoàn tất đánh giá mô hình học sinh! Các biểu đồ được lưu tại: {report_figs_path}")

In [ ]:
print("Bắt đầu quy trình phân tích Grad-CAM chi tiết...")

# --- BƯỚC 0: CHUẨN BỊ DỮ LIỆU VÀ CÁC BIẾN CẦN THIẾT ---
# Tải lại dữ liệu test một lần để sử dụng cho tất cả các mô hình
print("Đang tải và chuẩn bị dữ liệu test...")
test_ds_for_gradcam = tf.data.TFRecordDataset(TEST_TFREC)
test_ds_for_gradcam = test_ds_for_gradcam.map(parse_tfrecord_fn, num_parallel_calls=AUTOTUNE)
test_ds_for_gradcam = test_ds_for_gradcam.batch(GLOBAL_BATCH_SIZE)
test_ds_for_gradcam = test_ds_for_gradcam.prefetch(buffer_size=AUTOTUNE)

X_test_list = [images.numpy() for images, _ in test_ds_for_gradcam]
y_test_onehot_list = [labels.numpy() for _, labels in test_ds_for_gradcam]
X_test = np.concatenate(X_test_list, axis=0)
y_test_onehot = np.concatenate(y_test_onehot_list, axis=0)
y_test_encoded = np.argmax(y_test_onehot, axis=1)

target_names = le.classes_
last_conv_layer_name = "top_conv" # Lớp conv cuối của EfficientNet B0/B1
run_timestamp = datetime.datetime.now(pytz.timezone('Asia/Ho_Chi_Minh')).strftime("%Y%m%d_%H%M")

# Tạo thư mục chính để lưu kết quả
grad_cam_main_path = os.path.join(KAGGLE_OUTPUT_PATH, "grad_cam_detailed_analysis")
os.makedirs(grad_cam_main_path, exist_ok=True)


# --- HÀM HỖ TRỢ ĐỂ TÁI SỬ DỤNG CODE ---
def run_grad_cam_analysis_for_model(model, model_name, output_base_path):
    print(f"\n--- Bắt đầu phân tích cho mô hình: {model_name} ---")
    
    # 1. Lấy dự đoán từ mô hình
    print("  - Lấy dự đoán...")
    y_pred_probs = tf.nn.softmax(model.predict(X_test, batch_size=GLOBAL_BATCH_SIZE, verbose=0)).numpy()
    y_pred_encoded = np.argmax(y_pred_probs, axis=1)

    # 2. Tạo DataFrame kết quả
    results_list = []
    for i in range(len(y_test_encoded)):
        results_list.append({
            'index': i, 
            'true_label': y_test_encoded[i], 
            'pred_label': y_pred_encoded[i], 
            'confidence': y_pred_probs[i][y_pred_encoded[i]],
            'is_correct': y_test_encoded[i] == y_pred_encoded[i]
        })
    results_df = pd.DataFrame(results_list)

    # 3. Phân tích trên từng lớp
    for class_index, class_name in enumerate(target_names):
        print(f"    - Phân tích lớp: '{class_name}'...")
        class_output_path = os.path.join(output_base_path, class_name)
        os.makedirs(class_output_path, exist_ok=True)

        # Lọc các mẫu thuộc lớp hiện tại
        class_samples_df = results_df[results_df['true_label'] == class_index]
        correct_samples = class_samples_df[class_samples_df['is_correct'] == True]
        incorrect_samples = class_samples_df[class_samples_df['is_correct'] == False]
        
        # --- Tính Grad-CAM trung bình ---
        # Trung bình cho các mẫu ĐÚNG
        if not correct_samples.empty:
            correct_heatmaps = [get_grad_cam_final(model, X_test[i][np.newaxis, ...], last_conv_layer_name) for i in correct_samples['index']]
            avg_heatmap_correct = np.mean(correct_heatmaps, axis=0)
            overlay = overlay_grad_cam(np.zeros_like(X_test[0, :, :, 0]), avg_heatmap_correct)
            plt.imsave(os.path.join(class_output_path, f"{model_name}_{class_name}_avg_correct.png"), overlay)

        # Trung bình cho các mẫu SAI
        if not incorrect_samples.empty:
            incorrect_heatmaps = [get_grad_cam_final(model, X_test[i][np.newaxis, ...], last_conv_layer_name) for i in incorrect_samples['index']]
            avg_heatmap_incorrect = np.mean(incorrect_heatmaps, axis=0)
            overlay = overlay_grad_cam(np.zeros_like(X_test[0, :, :, 0]), avg_heatmap_incorrect)
            plt.imsave(os.path.join(class_output_path, f"{model_name}_{class_name}_avg_incorrect.png"), overlay)

        # --- Tìm các mẫu tự tin nhất ---
        # Mẫu ĐÚNG tự tin nhất
        if not correct_samples.empty:
            best_correct = correct_samples.loc[correct_samples['confidence'].idxmax()]
            idx = int(best_correct['index'])
            heatmap = get_grad_cam_final(model, X_test[idx][np.newaxis, ...], last_conv_layer_name)
            overlay = overlay_grad_cam(X_test[idx, :, :, 0], heatmap)
            plt.imsave(os.path.join(class_output_path, f"{model_name}_{class_name}_exemplar_correct.png"), overlay)
            
        # Mẫu SAI tự tin nhất
        if not incorrect_samples.empty:
            worst_incorrect = incorrect_samples.loc[incorrect_samples['confidence'].idxmax()]
            idx = int(worst_incorrect['index'])
            heatmap = get_grad_cam_final(model, X_test[idx][np.newaxis, ...], last_conv_layer_name)
            overlay = overlay_grad_cam(X_test[idx, :, :, 0], heatmap)
            plt.imsave(os.path.join(class_output_path, f"{model_name}_{class_name}_exemplar_incorrect.png"), overlay)


# ==============================================================================
# PHẦN 1: ĐÁNH GIÁ 5 MÔ HÌNH THẦY GIÁO
# ==============================================================================
teacher_models_path = os.path.join(grad_cam_main_path, "teacher_models")
os.makedirs(teacher_models_path, exist_ok=True)

for fold_number in range(1, N_SPLITS + 1):
    model_path = os.path.join(KAGGLE_OUTPUT_PATH, f'{MODEL_ID}_fold_{fold_number}.keras')
    with strategy.scope():
        teacher_model = tf.keras.models.load_model(model_path)
    
    model_name = f"fold_{fold_number}"
    fold_output_path = os.path.join(teacher_models_path, model_name)
    os.makedirs(fold_output_path, exist_ok=True)
    
    run_grad_cam_analysis_for_model(teacher_model, model_name, fold_output_path)


# ==============================================================================
# PHẦN 2: ĐÁNH GIÁ MÔ HÌNH HỌC SINH
# ==============================================================================
student_model_path = os.path.join(KAGGLE_OUTPUT_PATH, "student_model.keras")

if not os.path.exists(student_model_path):
    print(f"\n--- Không tìm thấy mô hình học sinh. Bỏ qua phân tích. ---")
else:
    with strategy.scope():
        student_model = tf.keras.models.load_model(student_model_path)
    
    student_model_output_path = os.path.join(grad_cam_main_path, "student_model")
    os.makedirs(student_model_output_path, exist_ok=True)
    
    run_grad_cam_analysis_for_model(student_model, "student_model", student_model_output_path)

print(f"\n\nĐã hoàn tất toàn bộ phân tích Grad-CAM chi tiết!")
print(f"Kết quả được lưu tại thư mục: {grad_cam_main_path}")